In [2]:
import json
import os
import torch

In [38]:
f = open("/lustre/fsn1/worksf/projects/rech/dki/ujo91el/datas/datasets/sequences/00/hierarchical.json",) 
data = json.load(f)
f.close()

In [39]:
data

{'0': '330',
 '1': '331',
 '2': '332',
 '3': '333',
 '4': '3130',
 '5': '3110',
 '6': '3160',
 '7': '3190',
 '8': '3120',
 '9': '3100',
 '10': '380',
 '11': '381',
 '12': '382',
 '13': '383',
 '14': '384',
 '15': '320',
 '16': '3910',
 '17': '3990',
 '18': '3900',
 '19': '3940',
 '20': '3920',
 '21': '321',
 '22': '322',
 '23': '323',
 '24': '3500',
 '25': '3550',
 '26': '3520',
 '27': '3521',
 '28': '3530',
 '29': '3510',
 '30': '3540',
 '31': '9340',
 '32': '9341',
 '33': '9342',
 '34': '9380',
 '35': '9260',
 '36': '9261',
 '37': '9200',
 '38': '9270',
 '39': '9250',
 '40': '9210',
 '41': '0290',
 '42': '9211',
 '43': '0291',
 '44': '9240',
 '45': '0292',
 '46': '0293',
 '47': '0250',
 '48': '0251',
 '49': '02350',
 '50': '0252',
 '51': '02300',
 '52': '02380',
 '53': '02310',
 '54': '02311',
 '55': '02370',
 '56': '0220',
 '57': '0221',
 '58': '0222',
 '59': '02490',
 '60': '02410',
 '61': '02480',
 '62': '02450',
 '63': '02430',
 '64': '02460',
 '65': '0210',
 '66': '0211',
 '67':

In [10]:
eval_seq = 22
eval_seq = '%02d' % eval_seq
f = open("/lustre/fsn1/worksf/projects/rech/dki/ujo91el/datas/datasets/sequences/" + eval_seq + "/hierarchical_indexing.json",) 
data = json.load(f)
f.close()
label_mapping = {v: k for k, v in data.items()}

with open("/lustre/fsn1/worksf/projects/rech/dki/ujo91el/datas/datasets/sequences/" + eval_seq + "/hierarchical.json", "w") as json_file   :
    json.dump(label_mapping, json_file)  

In [6]:
data2 = {v: k for k, v in data.items()}

In [7]:
data2["8730"]

'0'

In [8]:
eval_seq = 6
log3dnet_dir=os.getenv('LOG3DNET_DIR')
## ==== Kitti =====
print("kitti dataset")
#kitti_dir = os.getenv('WORKSF') + '/datas/datasets/'
kitti_dir = '/lustre/fsn1/worksf/projects/rech/dki/ujo91el/datas/datasets/'
eval_seq = '%02d' % eval_seq
sequence_path = kitti_dir + 'sequences/' + eval_seq + '/'
num_queries = 4541
embeddings = []

kitti dataset


In [12]:
eval_seq = 6
log3dnet_dir=os.getenv('LOG3DNET_DIR')
## ==== Kitti =====
print("kitti dataset")
#kitti_dir = os.getenv('WORKSF') + '/datas/datasets/'
kitti_dir = '/lustre/fsn1/worksf/projects/rech/dki/ujo91el/datas/datasets/'
eval_seq = '%02d' % eval_seq
sequence_path = kitti_dir + 'sequences/' + eval_seq + '/'
num_queries = 1101
embeddings = []
for query_idx in range(num_queries):
    #input_data = data_collator(torch.utils.data.Subset(eval_subset,range(query_idx, query_idx+1)))
    #ids = input_data['ids'][0]
    padded_string = str(query_idx).zfill(6)
    print(padded_string)
    #import pdb; pdb.set_trace()                
    log_desc = sequence_path + "/logg_desc/" + padded_string + '.pt'

    xx = torch.load(log_desc)
    #xx1 = torch.load(fname)
    embeddings.append(xx)

kitti dataset
000000
000001
000002
000003
000004
000005
000006
000007
000008
000009
000010
000011
000012
000013
000014
000015
000016
000017
000018
000019
000020
000021
000022
000023
000024
000025
000026
000027
000028
000029
000030
000031
000032
000033
000034
000035
000036
000037
000038
000039
000040
000041
000042
000043
000044
000045
000046
000047
000048
000049
000050
000051
000052
000053
000054
000055
000056
000057
000058
000059
000060
000061
000062
000063
000064
000065
000066
000067
000068
000069
000070
000071
000072
000073
000074
000075
000076
000077
000078
000079
000080
000081
000082
000083
000084
000085
000086
000087
000088
000089
000090
000091
000092
000093
000094
000095
000096
000097
000098
000099
000100
000101
000102
000103
000104
000105
000106
000107
000108
000109
000110
000111
000112
000113
000114
000115
000116
000117
000118
000119
000120
000121
000122
000123
000124
000125
000126
000127
000128
000129
000130
000131
000132
000133
000134
000135
000136
000137
000138
000139
000140

In [13]:
import os
import sys
import glob
import random
import numpy as np
import logging
import json
import torch
import math
import numpy as np
from sklearn.cluster import KMeans

def hierarchical_clustering(embeddings, c=100, cluster_count=10):
    """
    Perform hierarchical clustering on document embeddings and assign document IDs.

    Args:
        embeddings (np.ndarray): 2D array of document embeddings (num_docs x embedding_dim).
        c (int): Maximum number of documents in a cluster before further clustering is applied.
        cluster_count (int): Number of clusters to create at each level (default 10 for decimal tree).

    Returns:
        dict: A mapping from document index to their assigned identifier.
    """
    def cluster_recursive(embeddings, prefix=''):
        num_docs = embeddings.shape[0]
        
        # If the number of documents is less than or equal to c, assign an arbitrary number.
        if num_docs <= c:
            return {i: prefix + str(i) for i in range(num_docs)}
        
        # Perform k-means clustering
        kmeans = KMeans(n_clusters=min(cluster_count, num_docs))
        clusters = kmeans.fit_predict(embeddings)
        
        # Dictionary to store the final docid for each document
        docid_map = {}
        
        # Process each cluster recursively
        for cluster_id in range(min(cluster_count, num_docs)):
            # Get the embeddings belonging to the current cluster
            cluster_embeddings = embeddings[clusters == cluster_id]
            
            # Recursively cluster within each sub-cluster and append to the prefix
            cluster_docid_map = cluster_recursive(cluster_embeddings, prefix=prefix + str(cluster_id))
            # Map document IDs
            docid_map.update({doc_idx: cluster_docid_map[i] for i, doc_idx in enumerate(np.where(clusters == cluster_id)[0])})
        
        return docid_map
    
    # Start the recursive clustering from the top level
    return cluster_recursive(embeddings)

In [14]:
num_docs = num_queries  # Example number of documents
embedding_dim = 256  # Example embedding size (BERT embeddings)
emb_cpu = torch.stack(embeddings).detach().cpu().numpy()

docid_map = hierarchical_clustering(emb_cpu, c=100, cluster_count=10)
docid_map_pad = {int(k): v.zfill(6) for k, v in docid_map.items()}

json_path = sequence_path + '/hierarchical.json'
# # Print the generated identifiers
for doc_idx, doc_id in docid_map.items():
    print(f"Document {doc_idx}: Identifier {doc_id}")
with open(json_path, "w") as json_file   :
    json.dump(docid_map_pad, json_file)        

Document 276: Identifier 00
Document 277: Identifier 01
Document 278: Identifier 02
Document 279: Identifier 03
Document 280: Identifier 04
Document 281: Identifier 05
Document 282: Identifier 06
Document 283: Identifier 07
Document 284: Identifier 08
Document 285: Identifier 09
Document 286: Identifier 010
Document 287: Identifier 011
Document 288: Identifier 012
Document 289: Identifier 013
Document 290: Identifier 014
Document 291: Identifier 015
Document 292: Identifier 016
Document 293: Identifier 017
Document 294: Identifier 018
Document 295: Identifier 019
Document 296: Identifier 020
Document 297: Identifier 021
Document 298: Identifier 022
Document 299: Identifier 023
Document 300: Identifier 024
Document 301: Identifier 025
Document 302: Identifier 026
Document 303: Identifier 027
Document 304: Identifier 028
Document 305: Identifier 029
Document 307: Identifier 030
Document 1091: Identifier 031
Document 1092: Identifier 032
Document 1093: Identifier 033
Document 1094: Identi

In [15]:
ini_dict = docid_map_pad
rev_dict = {}
 
for key, value in ini_dict.items():
    rev_dict.setdefault(value, set()).add(key)
     
result = [key for key, values in rev_dict.items()
                              if len(values) > 1]
 
# printing result
print("duplicate values", str(result))

duplicate values ['000030', '000031', '000032', '000033', '000034', '000035', '000036', '000037', '000038', '000039', '000040']


In [173]:
data

{'550': '000000',
 '5110': '003176',
 '5100': '002735',
 '5111': '003177',
 '5190': '003172',
 '5150': '001648',
 '5170': '002747',
 '540': '000007',
 '541': '000008',
 '7620': '000009',
 '542': '000010',
 '4120': '000011',
 '4121': '000012',
 '4122': '000013',
 '4130': '000014',
 '4131': '000015',
 '4132': '000016',
 '4160': '000017',
 '4100': '000018',
 '4150': '000019',
 '4151': '000020',
 '4180': '000021',
 '4190': '000022',
 '4140': '000023',
 '4170': '000024',
 '4171': '000025',
 '4172': '000026',
 '4550': '000027',
 '4551': '000028',
 '4500': '000029',
 '4501': '000030',
 '4502': '000031',
 '4503': '000032',
 '4560': '000033',
 '4504': '000034',
 '4590': '000035',
 '4591': '000036',
 '4520': '000037',
 '4521': '000038',
 '4522': '000039',
 '4523': '000040',
 '4570': '000041',
 '4571': '000042',
 '4572': '000043',
 '4510': '000044',
 '4511': '000045',
 '4540': '000046',
 '4580': '000047',
 '4581': '000048',
 '4582': '000049',
 '4583': '000050',
 '4530': '000051',
 '4420': '000052

In [194]:
f = open("/lustre/fsn1/worksf/projects/rech/dki/ujo91el/datas/datasets/sequences/00/hierarchical.json",) 
data = json.load(f)
f.close()

ini_dict = data
rev_dict = {}
 
for key, value in ini_dict.items():
    rev_dict.setdefault(value, set()).add(key)
     
result = [key for key, values in rev_dict.items()
                              if len(values) > 1]
 
# printing result
print("duplicate values", str(result))

duplicate values []


# gpt

In [14]:
import numpy as np
from sklearn.cluster import KMeans

def elementwise_str_concat(prefix_list, suffix_list):
    return [str(prefix) + str(suffix) for prefix, suffix in zip(prefix_list, suffix_list)]

def reorder_to_original(J, X, clusters):
    # Créer une liste d'indices pour trier `J` selon l'ordre original des documents
    original_order = np.concatenate(clusters).argsort()
    # Réordonner `J` en utilisant cet ordre original
    return [J[i] for i in original_order]

def generate_semantic_ids(X, c=10):
    # Effectuer le clustering des documents en k=10 clusters
    k = 10
    kmeans = KMeans(n_clusters=k).fit(X)
    clusters = [np.where(kmeans.labels_ == i)[0] for i in range(k)]
    
    J = []
    for i in range(k):
        current_cluster_size = len(clusters[i])
        Jcurrent = [str(i)] * current_cluster_size
        
        if current_cluster_size > c:
            # Appliquer la fonction récursive à ce cluster
            sub_cluster_embeddings = X[clusters[i]]
            Jrest = generate_semantic_ids(sub_cluster_embeddings, c)
        else:
            # Générer des indices numériques pour les documents dans ce cluster
            Jrest = list(map(str, range(current_cluster_size)))
        
        # Concaténer les préfixes et les suffixes pour obtenir les identifiants du cluster
        Jcluster = elementwise_str_concat(Jcurrent, Jrest)
        J.extend(Jcluster)
    
    # Réordonner les identifiants pour correspondre à l'ordre original des documents
    J = reorder_to_original(J, X, clusters)
    
    return J

# Exemple d'utilisation (X étant un tableau de vecteurs d'embeddings de documents)
# X = np.array(...)  # Vos embeddings de documents ici
# ids = generate_semantic_ids(X)
# print(ids)

In [24]:
embeddings

[tensor([ 0.1114,  0.0132,  0.0230,  0.0302,  0.0008,  0.0343,  0.0159,  0.0100,
          0.0289,  0.0185,  0.0102, -0.0133,  0.0209,  0.0303,  0.0485,  0.0056,
          0.0132,  0.0984,  0.0238,  0.1019,  0.0834, -0.0161,  0.0284,  0.0325,
          0.0227,  0.0331,  0.1355, -0.0287,  0.0369,  0.0025,  0.0805,  0.0655,
          0.0230,  0.0238,  0.1402,  0.0030,  0.0521,  0.0538, -0.0116,  0.0913,
          0.0306, -0.0047,  0.0017, -0.0160,  0.0080, -0.0035,  0.0449, -0.0063,
          0.0302,  0.1019,  0.0030,  0.1085, -0.0283,  0.0399,  0.0242,  0.0507,
          0.0119,  0.0030, -0.0324,  0.0374,  0.0091,  0.0525, -0.0004,  0.0474,
          0.0008,  0.0834,  0.0521, -0.0283,  0.1582,  0.0411,  0.0607,  0.0806,
         -0.0208,  0.0232,  0.0624, -0.0650,  0.0069,  0.1393,  0.0835,  0.1928,
          0.0343, -0.0161,  0.0538,  0.0399,  0.0411,  0.0990,  0.1186,  0.0816,
         -0.0017,  0.0143,  0.0157,  0.0933,  0.0142, -0.0159, -0.0038,  0.1224,
          0.0159,  0.0284, -

In [22]:
import numpy as np
from sklearn.cluster import KMeans

def elementwise_str_concat(prefix_list, suffix_list):
    return [str(prefix) + str(suffix) for prefix, suffix in zip(prefix_list, suffix_list)]

def reorder_to_original(J, X, clusters):
    # Créer une liste d'indices pour trier `J` selon l'ordre original des documents
    original_order = np.concatenate(clusters).argsort()
    # Réordonner `J` en utilisant cet ordre original
    return [J[i] for i in original_order]

def generate_semantic_ids(X, c=10):
    # Effectuer le clustering des documents en k=10 clusters
    k = 10
    kmeans = KMeans(n_clusters=k).fit(X)
    clusters = [np.where(kmeans.labels_ == i)[0] for i in range(k)]
    
    J = []
    for i in range(k):
        current_cluster_size = len(clusters[i])
        Jcurrent = [str(i)] * current_cluster_size
        
        if current_cluster_size > c:
            # Appliquer la fonction récursive à ce cluster
            sub_cluster_embeddings = X[clusters[i]]
            Jrest = generate_semantic_ids(sub_cluster_embeddings, c)
        else:
            # Générer des indices numériques pour les documents dans ce cluster
            Jrest = list(map(str, range(current_cluster_size)))
        
        # Concaténer les préfixes et les suffixes pour obtenir les identifiants du cluster
        Jcluster = elementwise_str_concat(Jcurrent, Jrest)
        J.extend(Jcluster)
    
    # Réordonner les identifiants pour correspondre à l'ordre original des documents
    J = reorder_to_original(J, X, clusters)
    
    return J

# Exemple d'utilisation (X étant un tableau de vecteurs d'embeddings de documents)
# X = np.array(...)  # Vos embeddings de documents ici
# ids = generate_semantic_ids(X)
# print(ids)

In [25]:
emb_cpu = torch.stack(embeddings).detach().cpu().numpy()
ids = generate_semantic_ids(emb_cpu)
print(ids)

['0960', '0910', '0961', '0911', '0912', '0913', '0914', '0920', '0921', '0922', '0200', '0290', '0291', '0260', '0230', '0231', '0280', '0210', '0220', '0240', '0270', '0500', '0530', '0531', '0590', '0540', '0520', '0510', '0570', '0180', '0181', '0110', '0111', '0112', '0150', '0140', '0141', '0190', '0191', '0100', '0170', '0171', '0172', '0680', '0620', '0640', '0600', '0650', '0651', '0652', '0610', '0611', '0390', '0391', '9680', '0380', '0381', '0310', '0311', '0330', '0331', '0332', '0370', '0320', '0321', '0322', '0360', '9320', '9321', '9322', '9323', '9324', '96220', '96260', '96270', '96250', '96210', '96211', '96280', '96230', '96290', '96330', '96380', '96360', '96310', '96311', '96320', '96312', '96313', '96350', '9040', '9041', '9042', '9050', '9051', '9052', '9080', '9000', '9030', '9031', '9032', '9033', '0010', '0011', '0012', '50470', '50410', '50480', '50490', '50440', '5960', '5961', '5962', '5963', '4230', '5950', '5951', '5952', '5900', '5901', '5902', '5903', 

In [63]:
k=10
c=10

X = emb_cpu

kmeans = KMeans(n_clusters=k).fit(X)
clusters = [np.where(kmeans.labels_ == i)[0] for i in range(k)]

J = []
for i in range(k):
    current_cluster_size = len(clusters[i])
    Jcurrent = [str(i)] * current_cluster_size
    
    if current_cluster_size > c:
        # Appliquer la fonction récursive à ce cluster
        sub_cluster_embeddings = X[clusters[i]]
        Jrest = generate_semantic_ids(sub_cluster_embeddings, c)
     

    
    else:
        # Générer des indices numériques pour les documents dans ce cluster
        Jrest = list(map(str, range(current_cluster_size)))
    
    # Concaténer les préfixes et les suffixes pour obtenir les identifiants du cluster
    Jcluster = elementwise_str_concat(Jcurrent, Jrest)
    
    print("curr ", Jcurrent)
    print("rest ", Jrest)
    print("luster ", Jcluster)
    J.extend(Jcluster)

# Réordonner les identifiants pour correspondre à l'ordre original des documents



curr  ['0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0'

In [65]:
def allDifferent1D(lst):
    return len(lst) == len(set(lst))

True

In [67]:
allDifferent1D(J), J

(True,
 ['0810',
  '0850',
  '0811',
  '0851',
  '0852',
  '0890',
  '0891',
  '0500',
  '0501',
  '0550',
  '0551',
  '0502',
  '0730',
  '0160',
  '0590',
  '0591',
  '0592',
  '0593',
  '0520',
  '0521',
  '0522',
  '0523',
  '0524',
  '0525',
  '0560',
  '0561',
  '0562',
  '0563',
  '0564',
  '0565',
  '0566',
  '0567',
  '0568',
  '05120',
  '05180',
  '05100',
  '05170',
  '05140',
  '05130',
  '05131',
  '05160',
  '05110',
  '05190',
  '05150',
  '0540',
  '0541',
  '0542',
  '0543',
  '0544',
  '0545',
  '0546',
  '0547',
  '0580',
  '0581',
  '0582',
  '0583',
  '0584',
  '0585',
  '0320',
  '0321',
  '0070',
  '0010',
  '0011',
  '0012',
  '0013',
  '0050',
  '0051',
  '0052',
  '0090',
  '0040',
  '0041',
  '0820',
  '0821',
  '0530',
  '0531',
  '0532',
  '0533',
  '0534',
  '0535',
  '0536',
  '0260',
  '0150',
  '0151',
  '0100',
  '0101',
  '0190',
  '0191',
  '0192',
  '0630',
  '0631',
  '0632',
  '0620',
  '0621',
  '0622',
  '0623',
  '0600',
  '0601',
  '0602',
  

In [54]:
original_order = np.concatenate(clusters).argsort()

#return [J[i] for i in original_order]

In [56]:
len(original_order)

4541

In [52]:
J = reorder_to_original(J, X, clusters)

# verif duplicate
def allDifferent1D(lst):
    return len(lst) == len(set(lst))
allDifferent1D(J)


True

# gpt 2

In [16]:
def elementwise_str_concat(prefix_list, suffix_list):
    return [str(prefix) + str(suffix) for prefix, suffix in zip(prefix_list, suffix_list)]

def reorder_to_original(J, X, clusters):
    # Créer une liste d'indices pour trier `J` selon l'ordre original des documents
    original_order = np.concatenate(clusters).argsort()
    # Réordonner `J` en utilisant cet ordre original
    return [J[i] for i in original_order]

# verification duplicate
def allDifferent1D(lst):
    return len(lst) == len(set(lst))

def generate_semantic_ids(X, c=10):
    # Effectuer le clustering des documents en k=10 clusters et obtenir les labels directement
    k = 10
    
    labels = KMeans(n_clusters=k).fit_predict(X)
    
    # Grouper les indices des documents par label
    clusters = [np.where(labels == i)[0] for i in range(k)]
    
    J = []
    for i in range(k):
        current_cluster_size = len(clusters[i])
        Jcurrent = [str(i)] * current_cluster_size
        
        if current_cluster_size > c:
            # Appliquer la fonction récursive à ce cluster
            sub_cluster_embeddings = X[clusters[i]] # sélectionne les descripteurs du cluster courant
            Jrest = generate_semantic_ids(sub_cluster_embeddings, c) # génère les noms, récursif
            
        else:
            # Générer des indices numériques pour les documents dans ce cluster
            Jrest = list(map(str, range(current_cluster_size)))
        
        # Concaténer les préfixes et les suffixes pour obtenir les identifiants du cluster
        Jcluster = elementwise_str_concat(Jcurrent, Jrest)
        J.extend(Jcluster)
    
    # Réordonner les identifiants pour correspondre à l'ordre original des documents
    J = reorder_to_original(J, X, clusters) # réordonne les ids hierarichique selon l'ordre des descripteurs (et non des clusters)

    if allDifferent1D(ids) == False:
        print("Il y a des doublons !")

    return J

def save_semantic_ids():
    eval_seq = 6
    log3dnet_dir=os.getenv('LOG3DNET_DIR')
    ## ==== Kitti =====
    print("kitti dataset")
    #kitti_dir = os.getenv('WORKSF') + '/datas/datasets/'
    kitti_dir = '/lustre/fsn1/worksf/projects/rech/dki/ujo91el/datas/datasets/'
    eval_seq = '%02d' % eval_seq
    sequence_path = kitti_dir + 'sequences/' + eval_seq + '/'
    num_queries = 4541
    embeddings = []
    for query_idx in range(num_queries):
        #input_data = data_collator(torch.utils.data.Subset(eval_subset,range(query_idx, query_idx+1)))
        #ids = input_data['ids'][0]
        padded_string = str(query_idx).zfill(6)
        print(padded_string)
        #import pdb; pdb.set_trace()                
        log_desc = sequence_path + "/logg_desc/" + padded_string + '.pt'
    
        xx = torch.load(log_desc)
        #xx1 = torch.load(fname)
        embeddings.append(xx)


    emb_cpu = torch.stack(embeddings).detach().cpu().numpy()
    J = generate_semantic_ids(emb_cpu , c=10)
    docid_map = {k: J[k] for k in range(len(J)) } # creat dict
    for i in range(len(J)):
        print(f"Document {i}: Identifier {J[i]}")
        
    json_path = sequence_path + '/hierarchical.json'
    # # Print the generated identifiers
    for doc_idx, doc_id in docid_map.items():
        print(f"Document {doc_idx}: Identifier {doc_id}")
    
    with open(json_path, "w") as json_file   :
        json.dump(docid_map, json_file)  
    print("docid_map saved at ", json_path)


In [17]:
save_semantic_ids()

kitti dataset
000000
000001
000002
000003
000004
000005
000006
000007
000008
000009
000010
000011
000012
000013
000014
000015
000016
000017
000018
000019
000020
000021
000022
000023
000024
000025
000026
000027
000028
000029
000030
000031
000032
000033
000034
000035
000036
000037
000038
000039
000040
000041
000042
000043
000044
000045
000046
000047
000048
000049
000050
000051
000052
000053
000054
000055
000056
000057
000058
000059
000060
000061
000062
000063
000064
000065
000066
000067
000068
000069
000070
000071
000072
000073
000074
000075
000076
000077
000078
000079
000080
000081
000082
000083
000084
000085
000086
000087
000088
000089
000090
000091
000092
000093
000094
000095
000096
000097
000098
000099
000100
000101
000102
000103
000104
000105
000106
000107
000108
000109
000110
000111
000112
000113
000114
000115
000116
000117
000118
000119
000120
000121
000122
000123
000124
000125
000126
000127
000128
000129
000130
000131
000132
000133
000134
000135
000136
000137
000138
000139
000140

FileNotFoundError: [Errno 2] No such file or directory: '/lustre/fsn1/worksf/projects/rech/dki/ujo91el/datas/datasets/sequences/06//logg_desc/001101.pt'

In [18]:
emb_cpu = torch.stack(embeddings).detach().cpu().numpy()
generate_semantic_ids(emb_cpu , c=10)
docid_map = {J[k]: '%06d' % k for k in range(len(J)) } # creat dict
for i in range(len(J)):
    print(f"Document {i}: Identifier {J[i]}")

docid_map = {int(k): v.zfill(6) for k, v in docid_map.items()}

NameError: name 'ids' is not defined

In [156]:
docid_map.items()

dict_items([(3140, '000626'), (3141, '003582'), (3142, '000002'), (3130, '000628'), (3110, '000624'), (3131, '003584'), (3132, '000006'), (3100, '000627'), (3101, '000008'), (3102, '000009'), (3190, '003579'), (3120, '003583'), (3121, '000012'), (3170, '000625'), (440, '000014'), (441, '000015'), (442, '000016'), (443, '000017'), (490, '000018'), (491, '000019'), (492, '000020'), (4160, '002154'), (4100, '001134'), (4180, '000883'), (4120, '000024'), (4190, '002622'), (4140, '002684'), (450, '000027'), (451, '000028'), (430, '000029'), (431, '000030'), (432, '000031'), (460, '000032'), (461, '000033'), (462, '000034'), (4040, '000600'), (4080, '000592'), (4070, '000103'), (4050, '001240'), (4010, '001410'), (4030, '001424'), (470, '000041'), (471, '000042'), (472, '000043'), (473, '000044'), (474, '000045'), (420, '000046'), (421, '000047'), (422, '000048'), (423, '000049'), (424, '000050'), (540, '000051'), (541, '000052'), (542, '000053'), (543, '000054'), (570, '000055'), (571, '000

In [137]:
ids = generate_semantic_ids(embeddings)
print(ids)


TypeError: stack(): argument 'tensors' (position 1) must be tuple of Tensors, not numpy.ndarray

In [71]:
allDifferent1D(ids)

True

In [147]:
k = 10
labels = KMeans(n_clusters=k).fit_predict(X)

# Grouper les indices des documents par label
clusters = [np.where(labels == i)[0] for i in range(k)]

J = []
for i in range(k):
    current_cluster_size = len(clusters[i])
    Jcurrent = [str(i)] * current_cluster_size
    
    if current_cluster_size > c:
        # Appliquer la fonction récursive à ce cluster
        sub_cluster_embeddings = X[clusters[i]]
        Jrest = generate_semantic_ids(sub_cluster_embeddings, c)
    else:
        # Générer des indices numériques pour les documents dans ce cluster
        Jrest = list(map(str, range(current_cluster_size))) # liste de 0 à current_cluster_size < 100
    
    # Concaténer les préfixes et les suffixes pour obtenir les identifiants du cluster
    Jcluster = elementwise_str_concat(Jcurrent, Jrest) # "0" + "250" = "0250"
    J.extend(Jcluster) # ajoute les ids du cluster à J

# Réordonner les identifiants pour correspondre à l'ordre original des documents



ValueError: Found array with dim 3. KMeans expected <= 2.

In [118]:
clusters[3]

array([   0,    1,    2,    3,    4,    5,    6,    7,    8,    9,   10,
         11,   12,   13,  182,  450,  451,  452,  453,  454,  455,  456,
        458,  459,  460,  461,  462,  808,  809,  810,  811,  812,  813,
        814,  815,  816,  819,  820,  821,  822, 1023, 1024, 1025, 1092,
       1266, 1288, 1289, 1290, 1291, 1292, 1293, 1294, 1295, 1296, 1297,
       1298, 1299, 1300, 1301, 1302, 1303, 1304, 1306, 1307, 1308, 1309,
       1313, 1681, 1682, 1748, 1749, 1750, 1751, 1752, 1753, 1754, 2032,
       2033, 2035, 2036, 2037, 2038, 2091, 2092, 2093, 2094, 2095, 2096,
       2097, 2098, 2099, 2100, 2101, 2102, 2103, 2104, 2105, 2106, 2107,
       2108, 2109, 2110, 2111, 2112, 2113, 2114, 2115, 2116, 2117, 2118,
       2119, 2120, 2121, 2122, 2123, 2124, 2125, 2126, 2127, 2128, 2129,
       2130, 2131, 2132, 2133, 2134, 2135, 2136, 2137, 2138, 2139, 2140,
       2141, 2142, 2143, 2144, 2153, 2259, 2520, 2521, 2522, 2523, 2524,
       2525, 2526, 2528, 2529, 2530, 2531, 2532, 25

In [119]:
J = reorder_to_original(J, X, clusters)
J

['3140',
 '3141',
 '3142',
 '3130',
 '3110',
 '3131',
 '3132',
 '3100',
 '3101',
 '3102',
 '3190',
 '3120',
 '3121',
 '3170',
 '0440',
 '0441',
 '0442',
 '0443',
 '0490',
 '0491',
 '0492',
 '04160',
 '04100',
 '04180',
 '04120',
 '04190',
 '04140',
 '0450',
 '0451',
 '0430',
 '0431',
 '0432',
 '0460',
 '0461',
 '0462',
 '04040',
 '04080',
 '04070',
 '04050',
 '04010',
 '04030',
 '0470',
 '0471',
 '0472',
 '0473',
 '0474',
 '0420',
 '0421',
 '0422',
 '0423',
 '0424',
 '0540',
 '0541',
 '0542',
 '0543',
 '0570',
 '0571',
 '0572',
 '0573',
 '0530',
 '0531',
 '0532',
 '0533',
 '0500',
 '0501',
 '0520',
 '0590',
 '0591',
 '0300',
 '0301',
 '0302',
 '0380',
 '0381',
 '0382',
 '0780',
 '0781',
 '0782',
 '0783',
 '0784',
 '0785',
 '0770',
 '0771',
 '0772',
 '0740',
 '0741',
 '07290',
 '07240',
 '07291',
 '07230',
 '07280',
 '07220',
 '07270',
 '07250',
 '0050',
 '0051',
 '0052',
 '0053',
 '0054',
 '0000',
 '0080',
 '0081',
 '0082',
 '0083',
 '4070',
 '4071',
 '2550',
 '2551',
 '2552',
 '2553',

In [120]:
docid_map_pad = {J[k]: '%06d' % k for k in range(len(J)) }
for i in range(len(J)):
    print(f"Document {i}: Identifier {J[i]}")


Document 0: Identifier 3140
Document 1: Identifier 3141
Document 2: Identifier 3142
Document 3: Identifier 3130
Document 4: Identifier 3110
Document 5: Identifier 3131
Document 6: Identifier 3132
Document 7: Identifier 3100
Document 8: Identifier 3101
Document 9: Identifier 3102
Document 10: Identifier 3190
Document 11: Identifier 3120
Document 12: Identifier 3121
Document 13: Identifier 3170
Document 14: Identifier 0440
Document 15: Identifier 0441
Document 16: Identifier 0442
Document 17: Identifier 0443
Document 18: Identifier 0490
Document 19: Identifier 0491
Document 20: Identifier 0492
Document 21: Identifier 04160
Document 22: Identifier 04100
Document 23: Identifier 04180
Document 24: Identifier 04120
Document 25: Identifier 04190
Document 26: Identifier 04140
Document 27: Identifier 0450
Document 28: Identifier 0451
Document 29: Identifier 0430
Document 30: Identifier 0431
Document 31: Identifier 0432
Document 32: Identifier 0460
Document 33: Identifier 0461
Document 34: Ident

In [92]:
X[clusters[0]]

array([[ 0.14340129, -0.00573775,  0.0285979 , ..., -0.01626735,
         0.03761946,  0.14118241],
       [ 0.15807512,  0.03269902,  0.0252162 , ..., -0.01304082,
         0.04116134,  0.11470411],
       [ 0.11385424,  0.03559512,  0.06496029, ..., -0.00890138,
         0.03764211,  0.09877428],
       ...,
       [ 0.09868024,  0.08964177,  0.08817077, ..., -0.02380259,
         0.08010383,  0.03148099],
       [ 0.09383379,  0.10744997,  0.07642612, ..., -0.04547845,
         0.0657145 ,  0.08968291],
       [ 0.08771453,  0.09139968,  0.06467824, ..., -0.05547424,
         0.06276972,  0.06840073]])

In [49]:
import os
import sys
import glob
import random
import numpy as np
import logging
import json
import torch
import math
import numpy as np
from sklearn.cluster import KMeans
from module_loader_kitti_pose import load_poses_from_txt

def elementwise_str_concat(prefix_list, suffix_list):
    return [str(prefix) + str(suffix) for prefix, suffix in zip(prefix_list, suffix_list)]

def reorder_to_original(J, X, clusters):
    # Créer une liste d'indices pour trier `J` selon l'ordre original des documents
    original_order = np.concatenate(clusters).argsort()
    # Réordonner `J` en utilisant cet ordre original
    return [J[i] for i in original_order]

# verification duplicate
def allDifferent1D(lst):
    return len(lst) == len(set(lst))

def generate_semantic_ids(X, c=10):
    # Effectuer le clustering des documents en k=10 clusters et obtenir les labels directement
    k = 10
    
    labels = KMeans(n_clusters=k).fit_predict(X)
    
    # Grouper les indices des documents par label
    clusters = [np.where(labels == i)[0] for i in range(k)]
    
    J = []
    for i in range(k):
        current_cluster_size = len(clusters[i])
        Jcurrent = [str(i)] * current_cluster_size
        
        if current_cluster_size > c:
            # Appliquer la fonction récursive à ce cluster
            sub_cluster_embeddings = X[clusters[i]] # sélectionne les descripteurs du cluster courant
            Jrest = generate_semantic_ids(sub_cluster_embeddings, c) # génère les noms, récursif
            
        else:
            # Générer des indices numériques pour les documents dans ce cluster
            Jrest = list(map(str, range(current_cluster_size)))
        
        # Concaténer les préfixes et les suffixes pour obtenir les identifiants du cluster
        Jcluster = elementwise_str_concat(Jcurrent, Jrest)
        J.extend(Jcluster)
    
    # Réordonner les identifiants pour correspondre à l'ordre original des documents
    J = reorder_to_original(J, X, clusters) # réordonne les ids hierarichique selon l'ordre des descripteurs (et non des clusters)

    # verification duplicate
    def allDifferent1D(lst):
        return len(lst) == len(set(lst))
    if allDifferent1D(J) == False:
        print("Il y a des doublons !")

    return J

def compute_hierarchical_clustering(eval_seq = 6):
    log3dnet_dir=os.getenv('LOG3DNET_DIR')
    ## ==== Kitti =====
    print("kitti dataset")
    #kitti_dir = os.getenv('WORKSF') + '/datas/datasets/'
    #kitti_dir = os.getenv('WORKSF') + "/datas/datasets/"
    kitti_dir =  "/lustre/fsn1/worksf/projects/rech/dki/ujo91el/datas/datasets/"
    eval_seq = '%02d' % eval_seq
    sequence_path = kitti_dir + 'sequences/' + eval_seq + '/'
    _, positions_database = load_poses_from_txt(
            sequence_path + 'poses.txt')
    num_queries =  len(positions_database)
    embeddings = []
    for query_idx in range(num_queries):
        #ids = input_data['ids'][0]
        padded_string = str(query_idx).zfill(6)
        print(padded_string)
        #import pdb; pdb.set_trace()                
        log_desc = sequence_path + "/logg_desc/" + padded_string + '.pt'
    
        xx = torch.load(log_desc)
        #xx1 = torch.load(fname)
        embeddings.append(xx)

    emb_cpu = torch.stack(embeddings).detach().cpu().numpy()
    J = generate_semantic_ids(emb_cpu , c=10)
    docid_map = {k: J[k] for k in range(len(J)) } # creat dict
    for i in range(len(J)):
        print(f"Document {i}: Identifier {J[i]}")

    json_path = sequence_path + '/hierarchical.json'
    # # Print the generated identifiers
    for doc_idx, doc_id in docid_map.items():
        print(f"Document {doc_idx}: Identifier {doc_id}")
    
    with open(json_path, "w") as json_file   :
        json.dump(docid_map, json_file)  
    print("docid_map saved at ", json_path)

In [54]:
compute_hierarchical_clustering(8)

kitti dataset
000000
000001
000002
000003
000004
000005
000006
000007
000008
000009
000010
000011
000012
000013
000014
000015
000016
000017
000018
000019
000020
000021
000022
000023
000024
000025
000026
000027
000028
000029
000030
000031
000032
000033
000034
000035
000036
000037
000038
000039
000040
000041
000042
000043
000044
000045
000046
000047
000048
000049
000050
000051
000052
000053
000054
000055
000056
000057
000058
000059
000060
000061
000062
000063
000064
000065
000066
000067
000068
000069
000070
000071
000072
000073
000074
000075
000076
000077
000078
000079
000080
000081
000082
000083
000084
000085
000086
000087
000088
000089
000090
000091
000092
000093
000094
000095
000096
000097
000098
000099
000100
000101
000102
000103
000104
000105
000106
000107
000108
000109
000110
000111
000112
000113
000114
000115
000116
000117
000118
000119
000120
000121
000122
000123
000124
000125
000126
000127
000128
000129
000130
000131
000132
000133
000134
000135
000136
000137
000138
000139
000140